<a href="https://colab.research.google.com/github/kabianca/analise-de-sinistros/blob/main/AnaliseSinistros.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

Neste projeto será realizado uma análise descritiva do comportamento de um grupo de assegurados que foram convidados a fazer parte de um programa de prevenção de doenças crônicas. Serão revisadas as despesas e o número de reclamações dos participantes do programa. E, além disso, projetarei uma metodologia para validar se os objetivos do programa estão sendo atendidos. Por fim, validarei se há oportunidades de melhoria dentro do programa para que o negócio possa gerenciar melhor o custo.

Descrever a população de análise que é composta por pacientes com diagnóstico de diabetes, hipertensão ou ambos que pertencem ao programa de prevenção. Diagnosticar as despesas do programa, despesas totais, número de sinistros, ticket médio por assegurado, etc.

Como terceira tarefa, você terá que criar uma forma de validar se o objetivo do programa está sendo cumprido, podendo comparar com os indicadores dos assegurados que não estão no programa. Por fim, fazer recomendações para poder reduzir o custo do programa.


In [ ]:
from google.colab import files
uploaded = files.upload()

Saving laboratoria_salud.csv to laboratoria_salud.csv


In [ ]:
import io
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.figure_factory as ff

from plotly import graph_objects as go
from plotly.subplots import make_subplots
from datetime import timedelta

In [ ]:
# Dataset is now stored in a Pandas Dataframe
dfSaude = pd.read_csv(io.BytesIO(uploaded['laboratoria_salud.csv']), encoding='latin1')

In [ ]:
dfSaude

fec_ocurrencia   edad sexo estado_civil desc_producto_agrupado  \
0            11/09/18   43.0    F            S                    EPS   
1             9/05/17  101.0    F            C                    AMI   
2            20/10/18   57.0    F            S                    AMI   
3            23/04/18   58.0    M            C                    EPS   
4             8/05/17   75.0    F            C                    AMI   
...               ...    ...  ...          ...                    ...   
591534        2/02/16   74.0    M            C                    EPS   
591535       27/12/18   57.0    M            S                    EPS   
591536        9/07/16   79.0    F            C                    EPS   
591537        4/12/18   59.0    M            S                    EPS   
591538       12/11/18   60.0    M            C                    EPS   

       ind_capital_provincia         desc_tipo_contrat          agrupbenef  \
0                          P         PAGO POR SERVICIO         AMBULATORIO   
1                          L       PACIENTE MES HTA SP  PROGRAMAS CRONICOS   
2                          L         PAGO POR SERVICIO         AMBULATORIO   
3                          L      PACIENTE MES REGULAR         AMBULATORIO   
4                          L          PACIENTE MES HTA  PROGRAMAS CRONICOS   
...                      ...                       ...                 ...   
591534                     L  PACIENTE MES DIABETES SP  PROGRAMAS CRONICOS   
591535                     L       PACIENTE MES HTA SP  PROGRAMAS CRONICOS   
591536                     L       PACIENTE MES HTA SP  PROGRAMAS CRONICOS   
591537                     L  PACIENTE MES DIABETES SP  PROGRAMAS CRONICOS   
591538                     L       PACIENTE MES HTA SP  PROGRAMAS CRONICOS   

       cod_diagnostico                   agrupdiagno  beneficio_pagado  \
0                 I10X  HIPERTENSION ARTERIAL (N346)            175.94   
1                 I10X  HIPERTENSION ARTERIAL (N346)            201.85   
2                 E119      DIABETES MELLITUS (N166)            586.79   
3                 E109      DIABETES MELLITUS (N166)             45.43   
4                 I10X  HIPERTENSION ARTERIAL (N346)            121.00   
...                ...                           ...               ...   
591534            E119      DIABETES MELLITUS (N166)            290.85   
591535            I10X  HIPERTENSION ARTERIAL (N346)            201.85   
591536            I10X  HIPERTENSION ARTERIAL (N346)            201.85   
591537            E119      DIABETES MELLITUS (N166)            291.09   
591538            I10X  HIPERTENSION ARTERIAL (N346)            201.85   

        gasto_presentado  periodo    anio_ingreso   fecha_ingreso  \
0                 245.90     2018  No determinado  No determinado   
1                 718.51     2017            2016         3/05/16   
2                 733.49     2018            2016        30/01/16   
3                1075.27     2018  No determinado  No determinado   
4                 349.83     2017            2016         3/02/16   
...                  ...      ...             ...             ...   
591534            167.50     2016            2016         4/01/16   
591535           1142.25     2018            2018        23/10/18   
591536            332.30     2016            2016        20/01/16   
591537             35.00     2018            2016         3/03/16   
591538            195.30     2018            2016        15/01/16   

         agrup_CIE10  flag_programa  num_afiliado  
0       Hipertension              0             1  
1       Hipertension              1             2  
2           Diabetes              1             3  
3           Diabetes              0             4  
4       Hipertension              1             5  
...              ...            ...           ...  
591534      Diabetes              1          4502  
591535  Hipertension              1         19404  
591536 

In [ ]:
print(f'O dataframe conta com {dfSaude.shape[0]} linhas e {dfSaude.shape[1]} colunas')

O dataframe conta com 591539 linhas e 18 colunas


In [ ]:
# Visualizar o tipo de dados de cada variável:
dfSaude.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 591539 entries, 0 to 591538
Data columns (total 18 columns):
 #   Column                  Non-Null Count   Dtype  
---  ------                  --------------   -----  
 0   fec_ocurrencia          591539 non-null  object 
 1   edad                    588031 non-null  float64
 2   sexo                    588031 non-null  object 
 3   estado_civil            563567 non-null  object 
 4   desc_producto_agrupado  591539 non-null  object 
 5   ind_capital_provincia   591082 non-null  object 
 6   desc_tipo_contrat       591539 non-null  object 
 7   agrupbenef              591539 non-null  object 
 8   cod_diagnostico         591539 non-null  object 
 9   agrupdiagno             591539 non-null  object 
 10  beneficio_pagado        591539 non-null  float64
 11  gasto_presentado        591539 non-null  float64
 12  periodo                 591539 non-null  int64  
 13  anio_ingreso            591539 non-null  object 
 14  fecha_ingreso       

O resultado deste comando nos mostra cada uma das variáveis, o número de valores não nulos (não vazios) e o tipo da variável. Por exemplo, a variável edad possui 588.031 registros não nulos, ou seja, 3.508 estão vazios e o tipo de dados é "float".

Agora iremos conferir algumas estatísticas rápidas para validar valores extremos e consistência de dados. O resultado começa a nos mostrar estatísticas que chamam a atenção, como benefício_pagados negativos. Também temos assegurados com 0 anos de idade. É possível que um assegurado de 0 anos tenha diabetes ou hipertensão?


In [ ]:
dfSaude.describe()

edad  beneficio_pagado  gasto_presentado        periodo  \
count  588031.000000     591539.000000     591539.000000  591539.000000   
mean       63.049159        204.650653        385.151447    2017.055489   
std        14.112088        467.044516        595.640341       0.814907   
min         0.000000      -4017.220000          0.000000    2016.000000   
25%        54.000000        116.400000        154.295000    2016.000000   
50%        63.000000        152.500000        300.500000    2017.000000   
75%        72.000000        218.405500        494.300000    2018.000000   
max       107.000000     125491.790000     147637.390000    2018.000000   

       flag_programa   num_afiliado  
count  591539.000000  591539.000000  
mean        0.571071   14459.322319  
std         0.494924   12393.842645  
min         0.000000       1.000000  
25%         0.000000    5115.000000  
50%         1.000000   11184.000000  
75%         1.000000   20370.000000  
max         1.000000   60503.000000

In [ ]:
dfSaude.describe(include='all')

fec_ocurrencia           edad    sexo estado_civil  \
count          591539  588031.000000  588031       563567   
unique           1096            NaN       2            6   
top           9/10/18            NaN       M            C   
freq              999            NaN  327272       356855   
mean              NaN      63.049159     NaN          NaN   
std               NaN      14.112088     NaN          NaN   
min               NaN       0.000000     NaN          NaN   
25%               NaN      54.000000     NaN          NaN   
50%               NaN      63.000000     NaN          NaN   
75%               NaN      72.000000     NaN          NaN   
max               NaN     107.000000     NaN          NaN   

       desc_producto_agrupado ind_capital_provincia     desc_tipo_contrat  \
count                  591539                591082                591539   
unique                      3                     4                    14   
top                       EPS                     L  PACIENTE MES REGULAR   
freq                   458596                510996                154775   
mean                      NaN                   NaN                   NaN   
std                       NaN                   NaN                   NaN   
min                       NaN                   NaN                   NaN   
25%                       NaN                   NaN                   NaN   
50%                       NaN                   NaN                   NaN   
75%                       NaN                   NaN                   NaN   
max                       NaN                   NaN                   NaN   

                agrupbenef cod_diagnostico                   agrupdiagno  \
count               591539          591539                        591539   
unique                   4              71                             5   
top     PROGRAMAS CRONICOS            I10X  HIPERTENSION ARTERIAL (N346)   
freq                300668          350748                        364993   
mean                   NaN             NaN                           NaN   
std                    NaN             NaN                           NaN   
min                    NaN             NaN                           NaN   
25%                    NaN             NaN                           NaN   
50%                    NaN             NaN                           NaN   
75%                    NaN             NaN                           NaN   
max                    NaN             NaN                           NaN   

        beneficio_pagado  gasto_presentado        periodo anio_ingreso  \
count      591539.000000     591539.000000  591539.000000       591539   
unique               NaN               NaN            NaN            4   
top                  NaN               NaN            NaN         2016   
freq                 NaN               NaN            NaN       269640   
mean          204.650653        385.151447    2017.055489          NaN   
std           467.044516        595.640341       0.814907          NaN   
min         -4017.220000          0.000000    2016.000000          NaN   
25%           116.400000        154.295000    2016.000000          NaN   
50%           152.500000        300.500000    2017.000000          NaN   
75%           218.405500        494.300000    2018.000000          NaN   
max        125491.790000     147637.390000    2018.000000          NaN   

         fecha_ingreso   agrup_CIE10  flag_programa   num_afiliado  
count           591539        591539  591539.000000  591539.000000  
unique             908             2            NaN            NaN  
top     No determinado  Hipertension            NaN            NaN  
freq            253728        365125            NaN            NaN  
mean               NaN           NaN       0.571071   14459.322319  
std                NaN           NaN       0.494924   12393.842645  
min                NaN           NaN       0.000000       1.0000

Para analisar os dados que não agregarão à análise um primeiro passo é contar a quantidade de dados perdidos por coluna, para que possamos obter esses dados devemos aproveitar os benefícios de um DataFrame. Para tal, iremos aplicar a função isnull(), esta função avalia cada dado e retorna um True ou False, True quando o dado é perdido e False quando não é.

In [ ]:
dfSaude.isnull()

fec_ocurrencia   edad   sexo  estado_civil  desc_producto_agrupado  \
0                False  False  False         False                   False   
1                False  False  False         False                   False   
2                False  False  False         False                   False   
3                False  False  False         False                   False   
4                False  False  False         False                   False   
...                ...    ...    ...           ...                     ...   
591534           False  False  False         False                   False   
591535           False  False  False         False                   False   
591536           False  False  False         False                   False   
591537           False  False  False         False                   False   
591538           False  False  False         False                   False   

        ind_capital_provincia  desc_tipo_contrat  agrupbenef  cod_diagnostico  \
0                       False              False       False            False   
1                       False              False       False            False   
2                       False              False       False            False   
3                       False              False       False            False   
4                       False              False       False            False   
...                       ...                ...         ...              ...   
591534                  False              False       False            False   
591535                  False              False       False            False   
591536                  False              False       False            False   
591537                  False              False       False            False   
591538                  False              False       False            False   

        agrupdiagno  beneficio_pagado  gasto_presentado  periodo  \
0             False             False             False    False   
1             False             False             False    False   
2             False             False             False    False   
3             False             False             False    False   
4             False             False             False    False   
...             ...               ...               ...      ...   
591534        False             False             False    False   
591535        False             False             False    False   
591536        False             False             False    False   
591537        False             False             False    False   
591538        False             False             False    False   

        anio_ingreso  fecha_ingreso  agrup_CIE10  flag_programa  num_afiliado  
0              False          False        False          False         False  
1              False          False        False          False         False  
2              False          False        False          False         False  
3              False          False        False          False         False  
4              False          False        False          False         False  
...              ...            ...          ...            ...           ...  
591534         False          False        False          False         False  
591535         False          False        False          False         False  
591536         False          False        False          False         False  
591537         False          False        False          False         False  
591538         False          False        False          False         False  

[591539 rows x 18 columns]

Agora aplicaremos a função sum() ao DataFrame resultante e obteremos a quantidade de dados perdidos por coluna, isso é possível dado que os valores Boolean True/False são implicitamente 1 e 0.

In [ ]:
dfSaude.isnull().sum()

fec_ocurrencia                0
edad                       3508
sexo                       3508
estado_civil              27972
desc_producto_agrupado        0
ind_capital_provincia       457
desc_tipo_contrat             0
agrupbenef                    0
cod_diagnostico               0
agrupdiagno                   0
beneficio_pagado              0
gasto_presentado              0
periodo                       0
anio_ingreso                  0
fecha_ingreso                 0
agrup_CIE10                   0
flag_programa                 0
num_afiliado                  0
dtype: int64

## **Explorando a população de análise**
---

O conjunto de dados é um conjunto de dados transacional, ou seja, contém operações realizadas pelos assegurados (clientes) da seguradora. Nossa primeira tarefa será construir um DataFrame no nível assegurado com apenas os dados demográficos de cada um deles.

É importante saber quantos meses/anos de história temos a nossa disposição para realizar sua análise e isso pode ser obtido extraindo a data mínima e a data máxima da coluna "fec_ocurrencia". Porém, para trabalhar com datas de forma mais simples, será preciso transformar a coluna que, como vimos anteriormente, é do tipo Object para um tipo de dado Datetime.


In [ ]:
dfSaude['fec_ocurrencia'] = pd.to_datetime(dfSaude['fec_ocurrencia'], yearfirst=False)
dfSaude.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 591539 entries, 0 to 591538
Data columns (total 18 columns):
 #   Column                  Non-Null Count   Dtype         
---  ------                  --------------   -----         
 0   fec_ocurrencia          591539 non-null  datetime64[ns]
 1   edad                    588031 non-null  float64       
 2   sexo                    588031 non-null  object        
 3   estado_civil            563567 non-null  object        
 4   desc_producto_agrupado  591539 non-null  object        
 5   ind_capital_provincia   591082 non-null  object        
 6   desc_tipo_contrat       591539 non-null  object        
 7   agrupbenef              591539 non-null  object        
 8   cod_diagnostico         591539 non-null  object        
 9   agrupdiagno             591539 non-null  object        
 10  beneficio_pagado        591539 non-null  float64       
 11  gasto_presentado        591539 non-null  float64       
 12  periodo                 591539

In [ ]:
print(f'A data mínima do conjunto é {dfSaude["fec_ocurrencia"].min()} e a data máxima é {dfSaude["fec_ocurrencia"].max()}')

A data mínima do conjunto é 2016-01-01 00:00:00 e a data máxima é 2018-12-31 00:00:00


Com isso podemos validar que nosso conjunto de dados tem um total de 3 anos de histórico, correspondentes aos anos de 2016, 2017 e 2018.
Agora iremos analisar com quantos assegurados únicos iremos trabalhar, para isso usaremos nunique() que pode ser aplicado em um DataFrame ou Series.


In [ ]:
print(dfSaude.nunique())
print('-------')
print(f'O número de assegurados únicos é {dfSaude["num_afiliado"].nunique()}')

fec_ocurrencia              1096
edad                         106
sexo                           2
estado_civil                   6
desc_producto_agrupado         3
ind_capital_provincia          4
desc_tipo_contrat             14
agrupbenef                     4
cod_diagnostico               71
agrupdiagno                    5
beneficio_pagado          125094
gasto_presentado           98647
periodo                        3
anio_ingreso                   4
fecha_ingreso                908
agrup_CIE10                    2
flag_programa                  2
num_afiliado               60503
dtype: int64
-------
O número de assegurados únicos é 60503


Pronto, sabemos que existem 60.503 assegurados que geraram um total de 591.539 sinistros. Agora, é hora de escolher quais são essas variáveis demográficas que irão nos ajudar a descrever nossa população. Escolheremos as seguintes:

In [ ]:
dfSaude = dfSaude.sort_values(by=['fec_ocurrencia'], ignore_index=True)

In [ ]:
vars_demograficas= ['num_afiliado', 'edad', 'sexo', 'estado_civil','desc_producto_agrupado', 'ind_capital_provincia', 'flag_programa']

Agora iremos extrair os assegurados somente com essas colunas, a seleção de colunas específicas e/ ou alguns registros (linhas) são conhecidos como subconjunto. Antes de começar é importante analisar os passos que devemos seguir para alcançar o resultado esperado. Neste caso, interessa apenas ter um cadastro por assegurado com suas respectivas variáveis demográficas. Ou seja, devemos criar uma tabela com 60.503 assegurados. As etapas serão as seguintes:

- Selecionar as colunas demográficas e o número do afiliado. 
- Eliminar duplicatas (assumindo que as variáveis demográficas não são alteradas pelo assegurado)

In [ ]:
dfSaude_populacao = dfSaude[vars_demograficas].drop_duplicates()

dfSaude_populacao.head()

num_afiliado  edad sexo estado_civil desc_producto_agrupado  \
0         44728  47.0    F            C                    EPS   
1          8004  47.0    F            N                    EPS   
2          9478  76.0    F            S                    AMC   
3         37299  25.0    F            S                    AMI   
4         24961  56.0    M            C                    EPS   

  ind_capital_provincia  flag_programa  
0                     P              0  
1                     P              0  
2                     L              0  
3                     P              0  
4                     P              0

In [ ]:
dfSaude_populacao.shape

(63979, 7)

Neste momento, deveremos ter 60.503 assegurados, porém ao fazer o shape ele mostra que você tem 63.979 registros. O que pode ser causado isso?. É evidente que existem afiliados que aparecem mais de uma vez, para identificar um código específico usaremos value_counts().

In [ ]:
dfSaude_populacao['num_afiliado'].value_counts()

29955    4
18628    4
31332    4
4313     4
4251     4
        ..
5626     1
35880    1
16223    1
50820    1
36816    1
Name: num_afiliado, Length: 60503, dtype: int64

Alguns assegurados aparecem 4 vezes na base de dados. Para analisarmos o que está acontecendo faremos um filtro pelo assegurado com o código 16245 e faremos uma análise de seus 4 registros.

In [ ]:
dfSaude_populacao.loc[dfSaude_populacao['num_afiliado']==16245]

num_afiliado  edad sexo estado_civil desc_producto_agrupado  \
9989           16245  58.0    M          NaN                    AMC   
198141         16245  58.0    M          NaN                    AMC   
377811         16245   NaN  NaN          NaN                    AMC   
384634         16245  58.0    M          NaN                    AMC   

       ind_capital_provincia  flag_programa  
9989                       L              1  
198141                     P              1  
377811                     L              1  
384634                   NaN              1

O assegurado tem 4 registros, em um registro a idade não tem valor, o ind_capital_provincia mostra que o assegurado mudou de Província para capital (Lisboa). A solução da empresa é manter somente o último registro, para isso é importante que você se certifique que o DataFrame original esteja ordenado por data de ocorrência. E se o último registro for um dado vazio? É melhor que você mantenha os últimos dados não vazios da coluna. As coisas estão ficando um pouco mais complicadas.

In [ ]:
dfSaude_populacao['edad'] = dfSaude_populacao.groupby('num_afiliado')['edad'].transform(lambda v: v.ffill())

dfSaude_populacao.loc[dfSaude_populacao['num_afiliado']==16245]

num_afiliado  edad sexo estado_civil desc_producto_agrupado  \
9989           16245  58.0    M          NaN                    AMC   
198141         16245  58.0    M          NaN                    AMC   
377811         16245  58.0  NaN          NaN                    AMC   
384634         16245  58.0    M          NaN                    AMC   

       ind_capital_provincia  flag_programa  
9989                       L              1  
198141                     P              1  
377811                     L              1  
384634                   NaN              1

Como podemos observar a coluna "edad" para o assegurado 16245 não possui mais valores vazios ou nulos. Agora aplicaremos este procedimento para o resto das colunas (“sexo”, “estado_civil”, “desc_producto_agrupado”, “ind_capital_provincia”, “flag_programa”)

In [ ]:
dfSaude_populacao['sexo'] = dfSaude_populacao.groupby('num_afiliado')['sexo'].transform(lambda v: v.ffill())
dfSaude_populacao['estado_civil'] = dfSaude_populacao.groupby('num_afiliado')['estado_civil'].transform(lambda v: v.ffill())
dfSaude_populacao['desc_producto_agrupado'] = dfSaude_populacao.groupby('num_afiliado')['desc_producto_agrupado'].transform(lambda v: v.ffill())
dfSaude_populacao['ind_capital_provincia'] = dfSaude_populacao.groupby('num_afiliado')['ind_capital_provincia'].transform(lambda v: v.ffill())
dfSaude_populacao['flag_programa'] = dfSaude_populacao.groupby('num_afiliado')['flag_programa'].transform(lambda v: v.ffill())

Agora, nosso objetivo é manter o último registro para cada assegurado, para ter apenas um registro para cada assegurado. Podemos aproveitar a função drop_duplicates() novamente, mas diferente da primeira vez, adicionaremos alguns parâmetros. Abaixo iremos utilizar o parâmetro subconjunto, este parâmetro informa que desta coluna só poderemos ter um valor, ou seja, nenhum valor pode estar repetido, com o segundo parâmetro informamos as variáveis que desejamos manter, neste caso estamos dizendo que queremos manter o último registro. Ao final deveremos ter um total de 60.503 registros.

In [ ]:
dfSaude_populacao = dfSaude_populacao.drop_duplicates(subset=['num_afiliado'], keep='last')
dfSaude_populacao.shape

(60503, 7)

Pronto, agora temos um DataFrame no nível do assegurado com suas informações demográficas. É hora de explorar esses dados. Vamos começar com a variável "edad" e a melhor forma de entender e explorar os dados é por meio de gráficos. A variável "edad" é uma variável contínua, então poderíamos usar um histograma para descrevê-la.

In [ ]:
fig = px.histogram(dfSaude_populacao, x='edad', nbins=10,
                  text_auto=True, title='Distribuição de Assegurados por Idade',
                  labels = {'count': 'Número de assegurados'}
                  ).update_layout(yaxis_title='# assegurados')
fig.show()

In [ ]:
fig1 = px.pie(dfSaude_populacao, names = 'sexo', title = 'Distribuição de Assegurados por Gênero')
fig1.show()

In [ ]:
fig2 = px.histogram(dfSaude_populacao, x = 'sexo', text_auto=True)
fig2.show()

In [ ]:
fig3 = px.histogram(dfSaude_populacao[['edad', 'sexo']].dropna(),
                    x = 'edad', nbins=10, color='sexo', text_auto=True)

fig3.show()

## **Explorando os indicadores do programa**
---

Como segundo objetivo, a empresa quer saber os números do programa, e gostaria de responder a perguntas tais como: Quantos afiliados temos no programa? Quantos para diabetes? Quantos para hipertensão ou ambos? Quanto está sendo gasto no programa? Número de serviços por assegurado no programa?

Para tal iremos fazer gráficos evolutivos ao longo do tempo e precisaremos criar algumas variáveis de tempo a partir da data de ocorrência. Por exemplo, um par de colunas, uma que seja o ano da data da ocorrência e outra que esteja no formato “Ano - mês” a partir do nosso dataframe original.


In [ ]:
dfSaude['year'] = dfSaude['fec_ocurrencia'].dt.year
dfSaude['Ano-Mes'] = dfSaude['fec_ocurrencia'].dt.to_period('M')

Como o objetivo desta etapa é obter os números do programa, criaremos um novo DataFrame apenas com as declarações que foram geradas dentro do programa. Ao conversar com a empresa, ela nos informa que para identificar uma reclamação que pertence ao programa é preciso fazer dois filtros:

* Flag_cuidate == 1
* Agrupbenef == ‘PROGRAMAS CRONICOS’

In [ ]:
dfSaudeCuidado = dfSaude.loc[(dfSaude['agrupbenef']=='PROGRAMAS CRONICOS') & (dfSaude['flag_programa']==1)]
dfSaudeCuidado.shape

(298471, 20)

Um primeiro gráfico simples irá mostrar o número de sinistros por ano que o programa possui.

In [ ]:
fig4 = px.histogram(dfSaudeCuidado['year'].astype(str),
                    x='year', category_orders=dict(year=['2016', '2017', '2018']))

fig4.show()

Convertemos a coluna “year” para string (objeto) para que seja tratada como uma categoria e utilizamos **category_order** para indicar a ordem das categorias no gráfico. O gráfico acima mostra que o número de sinistros cresce ano após ano. Esse comportamento pode ser devido a duas coisas: 

1) você tem mais assegurados no programa ou 
2) seus assegurados têm mais sinistros. Para responder a essa hipótese , **o que você acha de obter o número de assegurados únicos atendidos por ano?.**

Para esta tarefa usaremos um GROUPBY por ano, e contaremos o número de registros, enquanto para a coluna num_membro faremos uma contagem de registros exclusivos, como uma contagem distinta ou uma contagem exclusiva.

In [ ]:
dfSaudeCuidadoYear = dfSaudeCuidado.groupby('year', as_index=False).agg({'num_afiliado':['nunique', 'count']})
dfSaudeCuidadoYear.columns = ['Year', 'Assegurados', 'Sinistros']
dfSaudeCuidadoYear['Year'] = dfSaudeCuidadoYear['Year'].astype(str)

dfSaudeCuidadoYear['sinistroXassegurado'] = dfSaudeCuidadoYear['Sinistros']/dfSaudeCuidadoYear['Assegurados']

dfSaudeCuidadoYear.head()

Year  Assegurados  Sinistros  sinistroXassegurado
0  2016         9197      83037             9.028705
1  2017        10284     101933             9.911805
2  2018        11836     113501             9.589473

No código acima temos:

* Linha 1: Aplica um groupby por “year”, o parâmetro as_index=False informa que você não deseja a coluna “year ” não é um índice, mas uma coluna.
* Linha 2: Atribuímos alguns nomes adequados a este DataFrame que você criou.
* Linha 3: Convertemos o tipo de dados da coluna Year para string ou objeto.
* Linha 4: Calculamos um #sinistro por Assegurado que é obtido dividindo o número de sinistros pelo número de Assegurados.

No DataFrame criado temos o número de assegurados atendidos, o número de sinistros e o número de sinistros por assegurado. Com base nesses dados, qual será a razão para o aumento dos sinistros anuais?

In [ ]:
fig5 = make_subplots(specs=[[{'secondary_y':True}]])

fig5.add_trace(
    go.Bar(
        x = dfSaudeCuidadoYear['Year'],
        y = dfSaudeCuidadoYear['Assegurados'],
        name = 'Assegurados'
    ),
    secondary_y=False
)

fig5.add_trace(
    go.Scatter(
        x = dfSaudeCuidadoYear['Year'],
        y = dfSaudeCuidadoYear['Sinistros'],
        name = 'Sinistros',
        mode = 'lines'
    ),
    secondary_y=True
)

fig5.update_layout(
    title_text = 'Tendencias programa cuidado por # assegurados e # sinistros',
    title_x = 0.45,
    legend = dict(orientation = 'h', xanchor = 'center', x = 0.45, y =1.11),
    yaxis_title = '# Assegurados',
    yaxis2_title = '# Sinistros',
    yaxis_color = 'blue',
    yaxis2_color = 'red',
)

fig5.show()

Estamos vendo alguns dados interessantes do programa. Como o programa convida pacientes diagnosticados com Diabetes e Hipertensão, que tal dividirmos os números por doença? Abaixo vamos visualizar os dados agrupados por ano e tipo de doença.

In [ ]:
dfGastoAnual = dfSaudeCuidado.groupby(['year', 'agrup_CIE10'],
                                      as_index=False).agg({'num_afiliado' : ['nunique', 'count'],
                                                           'gasto_presentado' : 'sum'
                                                          })

dfGastoAnual.columns = ['Ano', 'agrup_CIE10', 'Assegurados', 'Sinistros', 'Gastos']
dfGastoAnual['Ano'] = dfGastoAnual['Ano'].astype(str)

dfGastoAnual['Sinistro/Assegurado'] = dfGastoAnual['Sinistros']/dfGastoAnual['Assegurados']

dfGastoAnual

Ano   agrup_CIE10  Assegurados  Sinistros        Gastos  \
0  2016      Diabetes         3281      28587  8.489152e+06   
1  2016  Hipertension         7571      54450  1.875302e+07   
2  2017      Diabetes         3754      39984  1.198025e+07   
3  2017  Hipertension         8407      61949  2.350063e+07   
4  2018      Diabetes         4389      46737  1.377866e+07   
5  2018  Hipertension         9617      66764  2.471630e+07   

   Sinistro/Assegurado  
0             8.712892  
1             7.191917  
2            10.651039  
3             7.368740  
4            10.648667  
5             6.942290

1. O que você pode diferenciar entre os segurados dos diferentes programas?
2. Complemente sua análise com os gráficos que considerar necessários.

A empresa pediu para avaliar os gastos do cliente, podemos implementar diferentes metodologias, desta vez podemos aplicar algo semelhante a uma análise de coorte. Analisaremos o primeiro ano de gastos e, em seguida, o segundo ano de gastos para clientes com mais de dois anos de história. Faremos a análise para cada um dos programas (Diabetes e Hipertensão). É possível que existam segurados que pertençam a ambos os programas, para não sujar a comparação vamos retirar esses segurados.

Lembre-se de que há muitas maneiras de realizar uma transformação ou uma seleção. Na figura 36 mostramos uma forma, na primeira linha do código (você já conhece) você está selecionando as combinações das colunas “num_affiliado” e “agrup_CIE10”. Então na segunda linha, um groupby() é executado para o "num_affiliado" e usaremos uma função filter(), como o nome nos diz esta função é usada para filtrar aqueles registros cujo tamanho é maior que 1. Por fim, o resultado são todos os segurados que estão em ambos os programas. O próximo passo é excluir esses segurados.


In [ ]:
dfAsseguradoCIE10 = dfSaudeCuidado[['num_afiliado', 'agrup_CIE10']].drop_duplicates()
dfAssegurado_DiaHiper = dfAsseguradoCIE10.groupby('num_afiliado').filter(lambda x:len(x)>1)

In [ ]:
dfCuidadoNoDuplicados = dfSaudeCuidado.loc[
    ~dfSaudeCuidado['num_afiliado'].isin(dfAssegurado_DiaHiper['num_afiliado'])]

# Validando se todos foram excluidos
dfCuidadoNoDuplicados[['num_afiliado', 'agrup_CIE10'
                      ]].drop_duplicates().groupby('num_afiliado').filter(lambda x:len(x)>1)

Empty DataFrame
Columns: [num_afiliado, agrup_CIE10]
Index: []

In [ ]:
dfCuidadoNoDuplicados['desc_tipo_contrat'].value_counts()

PACIENTE MES HTA                67426
PACIENTE MES HTA SP             56836
PACIENTE MES DIABETES SP        32846
PACIENTE MES DIABETES           18310
PAGO POR SERVICIO                4344
PACIENTE MES HTA AMI              110
PACIENTE MES REGULAR                5
PACIENTE MES DISLIPIDEMIA SP        3
PACIENTE MES DIABETES AMI           1
PACIENTE MES DISLIPIDEMIA           1
Name: desc_tipo_contrat, dtype: int64

O resultado acima pode nos deixar um pouco confusos, HTA = Hipertensão, Diabetes é Diabetes obviamente. Mas existem alguns valores adicionais. A empresa poderá nos dá algumas respostas, tais como: SP se refere a “Sem protocolo”, isso significa que não há restrições de medicamentos para esses segurados. Por outro lado, informa que não deve haver outros contratos que não os de Diabetes e HTA. Então é hora de limpar um pouco o DataFrame. Logo, filtraremos nosso DataFrame pelos seguintes valores: ['PATIENT MONTH HTA','PATIENT MONTH HTA SP', 'PATIENT MONTH DIABETES SP','PATIENT MONTH DIABETES']

Próximos passos! Vamos analisar a despesa anual por segurado, mas é possível que um segurado tenha iniciado o programa e após 6 meses tenha que desistir por qualquer motivo, este segurado pode estar nos fornecendo dados errados. Para calcular uma data de saída, vamos supor que a data de saída de um segurado é a última data que ele teve atendimento. E se tivermos uma data de entrada e uma data de saída, podemos calcular a antiguidade do segurado no programa.


In [39]:
dfCuidadoNoDuplicados = dfCuidadoNoDuplicados.loc[(dfCuidadoNoDuplicados['desc_tipo_contrat']=='PACIENTE MES HTA') |
                                                  (dfCuidadoNoDuplicados['desc_tipo_contrat']=='PACIENTE MES HTA SP') | 
                                                  (dfCuidadoNoDuplicados['desc_tipo_contrat']=='PACIENTE MES DIABETES') |
                                                  (dfCuidadoNoDuplicados['desc_tipo_contrat']=='PACIENTE MES DIABETES SP')
                                                 ]
dfCuidadoNoDuplicados.shape

(175418, 20)

In [40]:
dfCuidadoNoDuplicados['fecha_ingreso'] = pd.to_datetime(dfCuidadoNoDuplicados['fecha_ingreso'])

#A data de saída será considerada como a data de registro mais recente
dfCuidadoNoDuplicados['fecha_salida'] = dfCuidadoNoDuplicados.groupby('num_afiliado')['fec_ocurrencia'].transform('max')

#Definindo a quanto tempo cada assegurado está no programa
dfCuidadoNoDuplicados['antiguedad'] = dfCuidadoNoDuplicados['fecha_salida'] - dfCuidadoNoDuplicados['fecha_ingreso']
dfCuidadoNoDuplicados['antiguedad'] = dfCuidadoNoDuplicados['antiguedad'] / timedelta(days=365)

In [41]:
dfCuidadoNoDuplicados

fec_ocurrencia   edad sexo estado_civil desc_producto_agrupado  \
15         2016-01-02   82.0    F            S                    EPS   
17         2016-01-02   67.0    F            S                    EPS   
20         2016-01-02   95.0    M            C                    EPS   
27         2016-01-02  102.0    M            C                    EPS   
28         2016-01-02   43.0    M            C                    EPS   
...               ...    ...  ...          ...                    ...   
591501     2018-12-31   60.0    M            N                    AMI   
591509     2018-12-31   58.0    F            C                    EPS   
591513     2018-12-31   66.0    M            C                    AMC   
591527     2018-12-31   65.0    F            S                    AMC   
591538     2018-12-31   65.0    F            D                    EPS   

       ind_capital_provincia         desc_tipo_contrat          agrupbenef  \
15                         L       PACIENTE MES HTA SP  PROGRAMAS CRONICOS   
17                         L          PACIENTE MES HTA  PROGRAMAS CRONICOS   
20                         L          PACIENTE MES HTA  PROGRAMAS CRONICOS   
27                         L       PACIENTE MES HTA SP  PROGRAMAS CRONICOS   
28                         L     PACIENTE MES DIABETES  PROGRAMAS CRONICOS   
...                      ...                       ...                 ...   
591501                     L  PACIENTE MES DIABETES SP  PROGRAMAS CRONICOS   
591509                     L       PACIENTE MES HTA SP  PROGRAMAS CRONICOS   
591513                     L  PACIENTE MES DIABETES SP  PROGRAMAS CRONICOS   
591527                     L          PACIENTE MES HTA  PROGRAMAS CRONICOS   
591538                     L          PACIENTE MES HTA  PROGRAMAS CRONICOS   

       cod_diagnostico                   agrupdiagno  ...  periodo  \
15                I10X  HIPERTENSION ARTERIAL (N346)  ...     2016   
17                I10X  HIPERTENSION ARTERIAL (N346)  ...     2016   
20                I10X  HIPERTENSION ARTERIAL (N346)  ...     2016   
27                I10X  HIPERTENSION ARTERIAL (N346)  ...     2016   
28                E119      DIABETES MELLITUS (N166)  ...     2016   
...                ...                           ...  ...      ...   
591501            E119      DIABETES MELLITUS (N166)  ...     2018   
591509            I10X  HIPERTENSION ARTERIAL (N346)  ...     2018   
591513            E119      DIABETES MELLITUS (N166)  ...     2018   
591527            I10X  HIPERTENSION ARTERIAL (N346)  ...     2018   
591538            I10X  HIPERTENSION ARTERIAL (N346)  ...     2018   

        anio_ingreso  fecha_ingreso   agrup_CIE10 flag_programa num_afiliado  \
15              2016     2016-04-01  Hipertension             1         3591   
17              2016     2016-01-02  Hipertension             1        36805   
20              2016     2016-02-01  Hipertension             1        12827   
27              2016     2016-02-01  Hipertension             1        13067   
28              2016     2016-01-02      Diabetes             1         1624   
...              ...            ...           ...           ...          ...   
591501          2018     2018-02-24      Diabetes             1        28223   
591509          2016     2016-11-01  Hipertension             1         2894   
591513          2016     2016-02-25      Diabetes             1        17165   
591527          2016     2016-02-24  Hipertension             1        12040   
591538          2016     2016-08-01  Hipertension             1        14179   

        year  Ano-Mes  fecha_salida antiguedad  
15      2016  2016-01    2018-11-09   2.608219  
17      2016  2016-01    2018-12-19   2.964384  
20      2016  2016-01    2018-12-14   2.868493  
27      2016  2016-01    2017-06-05   1.342466  
28      2016  2016-01    2017-10-23   1.808219  
...      ...      ...           ...        ...  
591501  2018  2018-12    2018-12-31   0.849315  

Agora com esses dados fica muito mais fácil filtrar para fazer os cálculos necessários. Por exemplo, obter as despesas dos afiliados do programa em seu primeiro ano. Para isso, criaremos um novo DataFrame com os seguintes filtros:

* Que sua antiguidade seja maior que 1, assim garantimos que ele tenha todo o primeiro ano.
* Que a antiguidade da atenção é menor que 1, então só mantemos as reivindicações de um ano.
* Que a antiguidade de serviço seja maior que 0, para evitar casos negativos.

Com este DataFrame, faremos um groupby por “num_affiliado” e “agrup_CIE10” e adicionaremos o “expense_presented”.

In [42]:
despesasPrimeiroAno = dfCuidadoNoDuplicados.loc[dfCuidadoNoDuplicados['antiguedad']>0]

In [43]:
despesasPrimeiroAno = despesasPrimeiroAno.groupby(['num_afiliado', 'agrup_CIE10'],
                                                  as_index=False).agg({'gasto_presentado' : 'sum'})

despesasPrimeiroAno

num_afiliado   agrup_CIE10  gasto_presentado
0                 3      Diabetes            169.10
1                 5  Hipertension           4835.01
2                11      Diabetes          26259.69
3                12  Hipertension          19925.09
4                15  Hipertension           2195.30
...             ...           ...               ...
10171         57297  Hipertension            611.84
10172         58151      Diabetes            714.14
10173         58633      Diabetes             42.04
10174         59879  Hipertension           1494.48
10175         60211  Hipertension             70.00

[10176 rows x 3 columns]

In [44]:
hiper_gasto = despesasPrimeiroAno.loc[despesasPrimeiroAno['agrup_CIE10']=='Hipertension', 'gasto_presentado']
diabetes_gasto = despesasPrimeiroAno.loc[despesasPrimeiroAno['agrup_CIE10']=='Diabetes', 'gasto_presentado']

hist_data = [hiper_gasto, diabetes_gasto]
group_labels = ['Hipertensão', 'Diabetes']

fig6 = ff.create_distplot(hist_data, group_labels, show_hist=False)
fig6.show()

Podemos ver que há um caso extremo em Hipertensão com um gasto anual de mais de 25.000. E a gente vê que a curva do Diabetes está um pouco para a direita, isso dá uma indicação de que em média a despesa de um segurado do programa de Diabetes é maior que a média de um segurado do programa de Hipertensão. A questão é: **como podemos “validar” essa hipótese?**

Para validar se a diferença que encontramos é significativa, você pode contar com um teste conhecido como t-test, você pode aprender um pouco mais sobre esse teste aqui ([teste t](https://www.jmp.com/es_pe/statistics-knowledge-portal/t-test.html)). A seguir, compartilhamos uma calculadora onde você pode inserir os dados de cada grupo e validar se a diferença é estatisticamente significativa.

[Calculadora teste t](https://www.graphpad.com/quickcalcs/ttest1/?format=SD)

Use a calculadora para validar a diferença. Precisamos calcular a média de cada grupo, o desvio padrão e o número de registros para cada grupo.

In [45]:
despesasPrimeiroAno.loc[despesasPrimeiroAno['gasto_presentado']<20000].groupby(['agrup_CIE10']
                                                                             ).agg({'gasto_presentado':['count', 'mean', 'std']})

gasto_presentado                          
                        count         mean          std
agrup_CIE10                                            
Diabetes                 2236  5506.128168  4631.673495
Hipertension             7674  5684.646899  4410.398366

__Diga-nos, a diferença de gastos entre os dois grupos é validada?.__

__Nota__: Este procedimento é conhecido como teste A/B. Idealmente, um teste A/B deve ser realizado em um contexto controlado, com ambos os grupos selecionados aleatoriamente (algo que não sabemos no momento pois não sabemos como é o processo de inscrição no programa). Quando trabalhamos em um ambiente projetado para um teste A/B, os dados gerados são conhecidos como Dados Experimentais, enquanto os dados gerados diariamente fora de um ambiente de teste são conhecidos como Dados Observacionais. Quando temos Dados Observacionais, a aleatoriedade pode ser perdida, então precisamos encontrar maneiras de validar se ambos os grupos são representativos. Aqui deixamos um curso um pouco avançado caso você esteja interessado no mundo dos experimentos ([curso](https://www.udacity.com/course/ab-testing--ud257)).

> 👩‍💻 **__Agora é a sua vez!__ **, Exercício 7: Você consegue mensurar como são os gastos do segurado em seu segundo ano no programa? Os segurados com protocolo gastam mais do que os segurados sem protocolo?

## **Validar se os objetivos do programa são alcançados**
---

Agora você precisa validar se os objetivos do programa foram atendidos, você pode reutilizar a mesma metodologia que vimos na seção 5. Abaixo detalhamos os passos que você pode seguir (você pode seguir outro caminho também).

* Calcular a data de entrada do segurado que não está no programa (Assuma que a data de entrada é a primeira data do sinistro)
* Calcule a data de saída do segurado. (Assuma que a data de partida é a última data de reclamação)
* Aplique a mesma metodologia para medir. Você poderia analisar quais possíveis vieses essa metodologia pode ter? Como você poderia melhorar?

Um dos objetivos do programa é reduzir sinistros complexos. Em conversa com a empresa, é indicado que aqueles em que a coluna “agrupbenef” seja EMERGÊNCIA ou HOSPITAL e se o “agrupbenef” for PACIENTE AMBIENTAL e a “despesa_apresentada” for maior que 1.500, então é considerada uma reivindicação complexa.

__Como você pode validar se o objetivo está sendo alcançado?__ Aqui estão algumas sugestões:

* De todos os segurados com mais de dois anos, veja quantos deles tiveram um sinistro complexo no 2º ano. Já para os segurados que estão fora do programa, o mesmo exercício, todos aqueles que estão no serviço há mais de 2 anos, quantos deles tiveram sinistro complexo no 2º ano.
* Reclamações complexas de quem está no programa têm um custo médio menor do que reclamações complexas de quem não está no programa.

## **Propostas para tornar o programa eficiente**
---

Em reunião um colaborador da seguradora comentou que está nos dois programas (Diabetes e Hipertensão). E quando eles têm o controle dele, um médico o visita e faz um check-up rápido e lembra de ter visto que a clínica lhe cobra duas visitas. Parece correto para você? Você poderia validar se isso está correto? Quantas atenções duplas foram geradas pelos dois programas no mesmo paciente?